In [1]:
import gym
import gym_watten
import numpy as np
from time import sleep


In [ ]:
%load_ext line_profiler

In [2]:
env = gym.make("Watten-v0")

WARN: gym.spaces.Box autodetected dtype as <class 'numpy.float32'>. Please provide explicit dtype.
WARN: Environment '<class 'gym_watten.envs.watten_env.WattenEnv'>' has deprecated methods. Compatibility code invoked.


In [3]:
obs, is_done = env.reset(), False

In [4]:
state = env.get_state()
org_obs = obs

In [ ]:
while not is_done:
    env.render('human')    
    obs, rew, is_done, _ = env.step(np.argmax(obs))
    print(rew)
    sleep(1)

In [ ]:
[card.id for card in env.cards]

In [ ]:
env.set_state(state)
is_done = False
obs = org_obs


In [6]:
def search(obs):
    global sample_outputs, sample_inputs, next_index
    state = env.get_state()
    n = len(env.players[env.current_player].hand_cards)   
    p = 0
    local_index = next_index
    next_index += 1
    
    for i in range(n):
        sample_inputs[local_index][i] = env.players[env.current_player].hand_cards[i].id
        obs, rew, is_done, _ = env.step(sample_inputs[local_index][i])
        if is_done:
            sample_outputs[local_index][i] = (rew[0] > 0) / n
        else:
            sample_outputs[local_index][i] = (1 - search(obs)) / n
        env.set_state(state)
        p += sample_outputs[local_index][i]
        
    if env.table_card is not None:
        sample_inputs[local_index][5] = env.table_card.id
    sample_inputs[local_index][6] = env.players[env.current_player].tricks
    sample_inputs[local_index][7] = env.players[1 - env.current_player].tricks
    return p 

In [117]:
def generate_training_data(iterations=1):
    global sample_outputs, sample_inputs,next_index
    sample_outputs = np.zeros((30000*iterations, 5))
    sample_inputs = np.zeros((30000*iterations, 8), dtype=int)
    next_index = 0
    
    for i in range(iterations):
        obs = env.reset()
        search(obs)
    
    sample_inputs = sample_inputs[:next_index]
    sample_outputs = sample_outputs[:next_index]
    sample_outputs = np.exp(sample_outputs) / np.expand_dims(np.sum(np.exp(sample_outputs), axis=-1), -1)
    return sample_inputs, sample_outputs

In [77]:
generate_training_data()

(array([[16, 17, 10, ...,  0,  0,  0],
        [12,  0,  1, ..., 16,  0,  0],
        [17, 10,  5, ...,  0,  1,  0],
        ...,
        [ 0,  0,  0, ..., 16,  2,  2],
        [16,  0,  0, ...,  0,  2,  2],
        [12,  0,  0, ..., 16,  2,  2]]),
 array([[0.19829211, 0.20140077, 0.19862287, 0.20095371, 0.20073055],
        [0.19911051, 0.19994187, 0.19994187, 0.20189523, 0.19911051],
        [0.21179142, 0.20174223, 0.21179142, 0.20742474, 0.16725019],
        ...,
        [0.2       , 0.2       , 0.2       , 0.2       , 0.2       ],
        [0.40460968, 0.14884758, 0.14884758, 0.14884758, 0.14884758],
        [0.2       , 0.2       , 0.2       , 0.2       , 0.2       ]]))

In [ ]:
env.render('human')    

In [ ]:
obs, rew, is_done, _ = env.step(2)

In [ ]:
%lprun -f search search(obs)

In [90]:
from keras.models import Sequential
from keras.layers import Dense, Activation
import keras.backend as K
from IPython.display import clear_output

In [121]:
# For a single-input model with 2 classes (binary classification):
def mean_pred(y_true, y_pred):
    return K.mean(K.equal(K.gather(y_true, K.argmax(y_true, axis=-1)), K.gather(y_true, K.argmax(y_pred, axis=-1))))

model = Sequential()
model.add(Dense(128, activation='relu', input_dim=8))
model.add(Dense(256, activation='relu'))
model.add(Dense(512, activation='relu'))
model.add(Dense(5, activation='softmax'))
model.compile(optimizer='rmsprop',
              loss='mean_squared_error',
              metrics=['accuracy', mean_pred])


In [122]:
while True:
    generate_training_data(100)    
    p = np.random.permutation(len(sample_inputs))
    sample_inputs, sample_outputs = sample_inputs[p], sample_outputs[p]
    
    clear_output()
    # Train the model, iterating on the data in batches of 32 samples
    model.fit(sample_inputs, sample_outputs, epochs=1, batch_size=64)

Epoch 1/1
 986240/1012572 [============================>.] - ETA: 1s - loss: 5.9957e-04 - acc: 0.6189 - mean_pred: 0.7497

KeyboardInterrupt: 

In [110]:
generate_training_data()

(array([[ 7, 16, 29, ...,  0,  0,  0],
        [12, 22, 14, ...,  7,  0,  0],
        [16, 29,  2, ...,  0,  1,  0],
        ...,
        [12, 22, 14, ...,  7,  0,  2],
        [12, 22, 14, ..., 16,  0,  2],
        [12, 22, 14, ..., 29,  0,  2]]),
 array([[0.20113484, 0.19913351, 0.2004655 , 0.19896763, 0.20029852],
        [0.20044451, 0.19933401, 0.20044451, 0.19988849, 0.19988849],
        [0.20901803, 0.2104746 , 0.20757155, 0.20901803, 0.16391778],
        ...,
        [0.2       , 0.2       , 0.2       , 0.2       , 0.2       ],
        [0.2       , 0.2       , 0.2       , 0.2       , 0.2       ],
        [0.2       , 0.2       , 0.2       , 0.2       , 0.2       ]]))

In [123]:
predict = model.predict(sample_inputs)

In [124]:
index = 0
for i in sample_outputs:
    if i[np.argmax(i)] != i[np.argmax(predict[index])]:
        print(i, predict[index], index)
        
    index+=1

[0.18533577 0.25865691 0.18533577 0.18533577 0.18533577] [0.2014133  0.19825248 0.20365599 0.19848135 0.19819684] 28
[0.20296356 0.20296356 0.22060191 0.18673549 0.18673549] [0.20039822 0.20148282 0.20069996 0.19896805 0.19845094] 55
[0.18533577 0.25865691 0.18533577 0.18533577 0.18533577] [0.20174451 0.19939478 0.20281947 0.19802727 0.19801405] 92
[0.23105884 0.20676053 0.23105884 0.16556089 0.16556089] [0.22497101 0.22544622 0.22451775 0.16237763 0.1626874 ] 99
[0.23121486 0.21871988 0.21871988 0.16567269 0.16567269] [0.22531383 0.22638077 0.2244229  0.16174918 0.16213332] 111
[0.22800198 0.19299951 0.19299951 0.19299951 0.19299951] [0.200529   0.20007727 0.20270906 0.19854005 0.19814463] 200
[0.20221592 0.20221592 0.20221592 0.19667611 0.19667611] [0.2020399  0.19748618 0.19934668 0.20213969 0.19898747] 203
[0.23105884 0.23105884 0.20676053 0.16556089 0.16556089] [0.22541197 0.22493458 0.22785833 0.16099583 0.16079928] 214
[0.19299951 0.22800198 0.19299951 0.19299951 0.19299951] [0.

[0.19299951 0.19299951 0.22800198 0.19299951 0.19299951] [0.20144986 0.19941838 0.20130104 0.19914235 0.19868839] 8137
[0.27790185 0.21643018 0.16855599 0.16855599 0.16855599] [0.2584267  0.26078647 0.16098706 0.15986644 0.15993331] 8173
[0.17703122 0.29187513 0.17703122 0.17703122 0.17703122] [0.20308107 0.19927844 0.19972035 0.19900282 0.19891736] 8207
[0.17703122 0.29187513 0.17703122 0.17703122 0.17703122] [0.20198737 0.19917    0.20088954 0.19891606 0.19903706] 8213
[0.19299951 0.22800198 0.19299951 0.19299951 0.19299951] [0.2023497  0.20196624 0.19949885 0.19804008 0.19814512] 8227
[0.20054548 0.20335027 0.19777938 0.20054548 0.19777938] [0.20113957 0.20037931 0.19932637 0.20047714 0.19867758] 8257
[0.20054548 0.20054548 0.20335027 0.19777938 0.19777938] [0.20010395 0.20271619 0.2015512  0.1978266  0.19780207] 8260
[0.18533577 0.25865691 0.18533577 0.18533577 0.18533577] [0.20304705 0.20136462 0.2002699  0.19762339 0.19769503] 8308
[0.22836149 0.21602071 0.22836149 0.16362816 0.1

[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.1948432  0.20840837 0.19849604 0.19920576 0.19904657] 14659
[0.23105884 0.23105884 0.20676053 0.16556089 0.16556089] [0.22276576 0.22255415 0.22334102 0.16582018 0.16551895] 14710
[0.20083391 0.19944406 0.19944406 0.20083391 0.19944406] [0.19365302 0.21362682 0.19794704 0.19737813 0.19739498] 14739
[0.22214348 0.22840063 0.22214348 0.16365621 0.16365621] [0.22064392 0.22196543 0.22330458 0.167244   0.16684216] 14783
[0.21673952 0.19394705 0.24221055 0.17355144 0.17355144] [0.22471617 0.22449881 0.22399388 0.16329964 0.16349153] 14861
[0.21190958 0.21190958 0.23681299 0.16968393 0.16968393] [0.22823782 0.22850072 0.222262   0.16008443 0.16091505] 14863
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.19175133 0.19816078 0.20474014 0.2026624  0.20268536] 14887
[0.22800198 0.19299951 0.19299951 0.19299951 0.19299951] [0.20086499 0.19782071 0.204911   0.1983183  0.19808501] 14900
[0.2136671  0.19658322 0.19658322 0.1965

[0.18533577 0.18533577 0.25865691 0.18533577 0.18533577] [0.20314848 0.19896398 0.2024509  0.19774032 0.19769634] 21509
[0.2093749  0.22133602 0.23398045 0.16765432 0.16765432] [0.22477184 0.2248529  0.22440195 0.16288857 0.16308467] 21543
[0.20676053 0.23105884 0.23105884 0.16556089 0.16556089] [0.2248962  0.22469719 0.22385518 0.16323572 0.16331576] 21613
[0.19665342 0.20502041 0.20219259 0.20219259 0.193941  ] [0.20217645 0.2001385  0.20181066 0.1979634  0.19791108] 21628
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.21236463 0.21503048 0.19174558 0.1903669  0.19049247] 21662
[0.22800198 0.19299951 0.19299951 0.19299951 0.19299951] [0.2030093  0.19781731 0.20439644 0.19738488 0.19739208] 21689
[0.27790185 0.21643018 0.16855599 0.16855599 0.16855599] [0.25718993 0.26203528 0.16082676 0.15991706 0.16003102] 21732
[0.20054548 0.20335027 0.20054548 0.19777938 0.19777938] [0.20245054 0.20157585 0.20056416 0.19775999 0.1976494 ] 21792
[0.19299951 0.22800198 0.19299951 0.1929

[0.21871988 0.21871988 0.23121486 0.16567269 0.16567269] [0.22520632 0.22541533 0.22422254 0.16243558 0.16272026] 27880
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.20049527 0.22159931 0.19200225 0.19293556 0.19296767] 27894
[0.19299951 0.22800198 0.19299951 0.19299951 0.19299951] [0.20218605 0.19960615 0.20001388 0.19893357 0.1992603 ] 27910
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.21520494 0.2271301  0.1873644  0.18534878 0.1849518 ] 27932
[0.20175378 0.19994059 0.20021848 0.20021848 0.19786868] [0.20010373 0.20128247 0.20056933 0.19918008 0.19886439] 27956
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.2149006  0.21920417 0.18865366 0.18853953 0.18870202] 27976
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.19795108 0.19996993 0.20136559 0.20036379 0.20034961] 28081
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.2564999  0.2576144  0.1623536  0.16179392 0.16173816] 28083
[0.17703122 0.29187513 0.17703122 0.1770

...

[0.25865691 0.18533577 0.18533577 0.18533577 0.18533577] [0.19968393 0.20173728 0.2018957  0.19829088 0.19839214] 984477
[0.2093749  0.22133602 0.23398045 0.16765432 0.16765432] [0.22490163 0.22516881 0.22449465 0.16261886 0.16281603] 984482
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.20893645 0.21367238 0.1927796  0.19236974 0.19224179] 984496
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.21482593 0.21797241 0.18863657 0.18931141 0.18925366] 984543
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.20082623 0.19522436 0.20164585 0.20100228 0.20130126] 984554
[0.18533577 0.25865691 0.18533577 0.18533577 0.18533577] [0.20183094 0.19742842 0.20617819 0.19729494 0.19726752] 984569
[0.19299951 0.22800198 0.19299951 0.19299951 0.19299951] [0.20201904 0.19759236 0.20390086 0.19841303 0.19807468] 984572
[0.19831263 0.19694023 0.20531943 0.20248748 0.19694023] [0.19953968 0.20317568 0.20036596 0.19853072 0.19838794] 984587
[0.20847886 0.209204   0.209204 

[0.19299951 0.22800198 0.19299951 0.19299951 0.19299951] [0.20260154 0.19898494 0.20059285 0.19883241 0.19898827] 990429
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.19595739 0.2217242  0.19390248 0.19412051 0.19429544] 990491
[0.19299951 0.22800198 0.19299951 0.19299951 0.19299951] [0.20174003 0.20173463 0.19938804 0.19859496 0.19854225] 990534
[0.21871988 0.21871988 0.23121486 0.16567269 0.16567269] [0.22472101 0.22427565 0.2238327  0.163489   0.16368161] 990552
[0.18981583 0.22424091 0.2063116  0.18981583 0.18981583] [0.20225139 0.19941485 0.20221543 0.19817111 0.19794725] 990554
[0.27790185 0.21643018 0.16855599 0.16855599 0.16855599] [0.2558346  0.25797653 0.1622765  0.16188759 0.16202469] 990572
[0.19658322 0.2136671  0.19658322 0.19658322 0.19658322] [0.20236944 0.20196772 0.20081216 0.19747946 0.19737126] 990575
[0.19299951 0.19299951 0.22800198 0.19299951 0.19299951] [0.20320997 0.20072864 0.20080237 0.1976245  0.19763458] 990599
[0.29187513 0.17703122 0.1770312

[0.18533577 0.18533577 0.25865691 0.18533577 0.18533577] [0.20410582 0.19925368 0.20166941 0.19750945 0.19746159] 997161
[0.23121486 0.21871988 0.21871988 0.16567269 0.16567269] [0.2248336  0.22524323 0.22436176 0.16268729 0.16287413] 997217
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.20943415 0.21603213 0.19133215 0.19159381 0.19160771] 997232
[0.17703122 0.29187513 0.17703122 0.17703122 0.17703122] [0.207385   0.20588553 0.19590442 0.1952922  0.19553284] 997271
[0.21643018 0.27790185 0.16855599 0.16855599 0.16855599] [0.2565435  0.2541786  0.16554151 0.16200691 0.16172947] 997296
[0.17703122 0.29187513 0.17703122 0.17703122 0.17703122] [0.20202067 0.19952255 0.20023477 0.1990224  0.19919966] 997319
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.20093103 0.2137364  0.19514848 0.19500075 0.19518338] 997339
[0.27790185 0.21643018 0.16855599 0.16855599 0.16855599] [0.25687274 0.26284003 0.16079211 0.15970173 0.15979342] 997343
[0.17703122 0.29187513 0.1770312

[0.19299951 0.19299951 0.22800198 0.19299951 0.19299951] [0.20144986 0.19941838 0.20130104 0.19914235 0.19868839] 1003102
[0.17703122 0.29187513 0.17703122 0.17703122 0.17703122] [0.21184817 0.20741878 0.19361556 0.19365004 0.19346741] 1003132
[0.21190958 0.23681299 0.21190958 0.16968393 0.16968393] [0.22567686 0.225084   0.22748345 0.1609617  0.16079393] 1003133
[0.22836149 0.21602071 0.22836149 0.16362816 0.16362816] [0.2259149  0.22683255 0.22129636 0.1626722  0.16328405] 1003220
[0.19777173 0.2033424  0.19777173 0.2033424  0.19777173] [0.20313749 0.19884402 0.19956508 0.20046163 0.1979918 ] 1003235
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.21313137 0.22220486 0.18835887 0.18807843 0.18822637] 1003255
[0.2136671  0.19658322 0.19658322 0.19658322 0.19658322] [0.19984742 0.19955273 0.20547293 0.1976831  0.1974439 ] 1003295
[0.17703122 0.29187513 0.17703122 0.17703122 0.17703122] [0.2599476  0.257448   0.16127032 0.1606798  0.16065432] 1003329
[0.27790185 0.21643018 0

[0.21602071 0.22836149 0.22836149 0.16362816 0.16362816] [0.22563688 0.22515312 0.22500324 0.16203836 0.16216847] 1010749
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.21121198 0.2585069  0.17725164 0.1763962  0.17663325] 1010756
[0.29187513 0.17703122 0.17703122 0.17703122 0.17703122] [0.20097454 0.19646205 0.20148697 0.20056413 0.20051226] 1010768
[0.19299951 0.19299951 0.22800198 0.19299951 0.19299951] [0.19938709 0.20213316 0.20165987 0.19854088 0.19827905] 1010793
[0.27790185 0.21643018 0.16855599 0.16855599 0.16855599] [0.25717497 0.26359302 0.1605342  0.15931351 0.15938435] 1010818
[0.21871988 0.23121486 0.21871988 0.16567269 0.16567269] [0.22560708 0.22536077 0.22591059 0.16145748 0.16166408] 1010835
[0.20700004 0.20953102 0.2098951  0.20521094 0.1683629 ] [0.20896706 0.20638566 0.20757848 0.20975159 0.16731723] 1010972
[0.23619443 0.23619443 0.18912972 0.16924071 0.16924071] [0.2256768  0.2255268  0.22629915 0.16126417 0.16123313] 1011006
[0.21190958 0.23681299 0

In [101]:
sample_outputs[9]

array([0.2, 0.2, 0.2, 0.2, 0.2])